In [ ]:
!pip install pytdc==1.1.5
!pip install torch

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 151.2/151.2 kB 3.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.7/43.7 kB 3.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.8/46.8 kB 3.2 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of s3fs to determine which version is compatible with other requirements. This could take a while.
  Preparing metadata (setup.py) ... done
INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 315.1/315.1 kB 12.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.0/52.0 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.6/9.6 MB 57.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 38.4 MB/s eta 0:0

In [ ]:
from tdc.resource.pinnacle import PINNACLE
from tdc.benchmark_group import scdti_group

pinnacle = PINNACLE()
embeds = pinnacle.get_embeds()

Downloading...
100%|██████████| 2.57M/2.57M [00:00<00:00, 15.5MiB/s]
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 2.47MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:07<00:00, 26.4MiB/s]
Downloading...
100%|██████████| 20.5M/20.5M [00:00<00:00, 21.9MiB/s]


In [ ]:
import torch

# pandas row to Torch tensor
def row_to_tensor(row):
    return torch.tensor(row.values.tolist())

# adds Single Cell Drug Target Identification information from TDC to training data
def generate_data_target(train):
    for _, row in train.iterrows():
        try:
            prot = row["name"]
            ct = row["cell_type_label"]
            idx = "{}--{}".format(prot, ct)
            embed = embeds.loc[[idx]]
            target = row["y"]
            yield row_to_tensor(embed), torch.FloatTensor([[target]])
        except KeyError:
            print(f"{idx} was not found, continuing")
            target = row["y"]
            yield [], torch.FloatTensor([[target]])

def get_train_dev_test(seed=1):
  group = scdti_group.SCDTIGroup()
  train_val = group.get_train_valid_split(seed=seed)
  assert "train" in train_val, "no training set"
  assert "val" in train_val, "no validation set"
  assert len(train_val["train"]) > 0, "no entries in training set"
  tst = group.get_test(seed)["test"]
  return train_val["train"], train_val["val"], tst

In [ ]:
graph = pinnacle.get_ppi()

In [ ]:
# get predictions over all diseases and seeds
import pandas as pd
threshold = 0.5 # arbitrary
grouped = graph.groupby('Protein A')['Protein B'].apply(set).reset_index()
grouped.columns = ['Protein A', 'connected_proteins']
group = scdti_group.SCDTIGroup()
out = []

from google.colab import drive
try:
  drive.mount('/content/drive')
except:
  pass

for seed in range(1,11):
    train, dev, test = get_train_dev_test(seed=seed)
    full = pd.concat([train, dev, test], axis=0, ignore_index=True)
    full_ra = full[full["disease"] == "RA"]
    full_ibd = full[full["disease"] == "IBD"]
    name_counts_ra = full_ra['name'].value_counts().to_dict()
    name_counts_ibd = full_ibd['name'].value_counts().to_dict()
    olabels_ra = {x["name"]:x["y"] for _, x in full_ra.iterrows()}
    olabels_ibd = {x["name"]:x["y"] for _, x in full_ibd.iterrows()}
    labels_ra = olabels_ra.copy()
    labels_ibd = olabels_ibd.copy()
    test_set_labels_ra = {k:None for k,v in olabels_ra.items() if k in test[test["disease"] == "RA"]["name"].values}
    test_set_labels_ibd = {k:None for k,v in olabels_ibd.items() if k in test[test["disease"] == "IBD"]["name"].values}
    for i in range(10):
      new_labels_ra = labels_ra.copy()
      new_labels_ibd = labels_ibd.copy()
      for protein in labels_ra:
        if protein not in test_set_labels_ra:
          continue # leave train set labels as they are
        try:
          neighbors = grouped[grouped['Protein A'] == protein]['connected_proteins'].iloc[0]
        except:
          continue
        neighbors = [x for x in neighbors if x in labels_ra]
        if not neighbors: # protein must be in the disease set
          continue
        # remove test set None(s)
        neighbors = [x for x in neighbors if test_set_labels_ra.get(x,1) is not None]
        if not neighbors:
          continue
        num = sum(labels_ra.get(n,0)*name_counts_ra.get(n,0) for n in neighbors)
        denom = sum(name_counts_ra.get(n,0) if n in labels_ra else 0 for n in neighbors)
        assert num <= denom, f"{num} > {denom}"
        new_labels_ra[protein] = (num / denom) > threshold
        test_set_labels_ra[protein] = new_labels_ra[protein]
      if labels_ra == new_labels_ra:
        print(f"Converged after {i} iterations for RA in seed {seed}")
        break
      labels_ra = new_labels_ra
      for protein in labels_ibd:
        if protein not in test_set_labels_ibd:
          continue # leave train set labels as they are
        try:
          neighbors = grouped[grouped['Protein A'] == protein]['connected_proteins'].iloc[0]
        except:
          continue
        neighbors = [x for x in neighbors if x in labels_ibd]
        if not neighbors: # protein must be in the disease set
          continue
        # remove test set None(s)
        neighbors = [x for x in neighbors if test_set_labels_ibd.get(x,1) is not None]
        if not neighbors:
          continue
        num = sum(labels_ibd.get(n,0)*name_counts_ibd.get(n,0) for n in neighbors)
        denom = sum(name_counts_ibd.get(n,0) if n in labels_ibd else 0 for n in neighbors)
        assert num <= denom, f"{num} > {denom}"
        new_labels_ibd[protein] = (num / denom) > threshold
        test_set_labels_ibd[protein] = new_labels_ibd[protein]
      if labels_ibd == new_labels_ibd:
        print(f"Converged after {i} iterations for IBD in seed {seed}")
        break
      labels_ibd = new_labels_ibd
      # now create preds dataframe
      test["preds"] = test.apply(lambda x: test_set_labels_ra[x["name"]] if x["disease"] == "RA" else test_set_labels_ibd[x["name"]], axis=1)
      import pandas as pd
      test["preds"] = test.apply(lambda x: x["preds"] if not pd.isna(x["preds"]) else not x["y"], axis=1)
      test["preds"] = test["preds"].astype(int)
      res = group.evaluate(test, seed=seed)
      print(f"{res} at seed {seed}")
      out.append(res)
      test.to_csv(f'/content/drive/MyDrive/pinnacle_scdti_label_prop/test_dataframe_scdti_label_prop_seed{seed}.csv', index=False)
      # test.to_csv(f'test_dataframe_scdti_label_prop_seed{seed}.csv', index=False)
out


Found local copy...
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 1.78MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:03<00:00, 56.0MiB/s]
Downloading...
100%|██████████| 20.5M/20.5M [00:00<00:00, 48.4MiB/s]
Found local copy...
Loading...
Found local copy...
Loading...
Found local copy...


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Found local copy...
Downloading...


downloading pinancle zip data...


100%|██████████| 5.20M/5.20M [00:00<00:00, 21.4MiB/s]
Extracting zip file...
Done!


...

Downloading...


downloading pinancle zip data...


100%|██████████| 6.53M/6.53M [00:00<00:00, 26.0MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_test_preds_myeloid dendritic cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_val_preds_eye photoreceptor cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_lacrimal gland functional unit cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_intestinal crypt stem cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_intermediate monocyte.csv
got file TS_EFO_0000685_torch_mlp_all_preds_cardiac endothelial cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_myofibroblast cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_erythroid progenitor.csv
got file TS_EFO_0000685_torch_mlp_test_preds_cardiac muscle cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_all_preds_retinal pigment epithelial cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_respiratory goblet cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_hepatocyte.csv
got file TS_EFO_0003767_torch_

[{'IBD': 0.255, 'RA': 0.17000000000000004},
 {'IBD': 0.28666666666666674, 'RA': 0.1},
 {'IBD': 0.265, 'RA': 0.07999999999999999},
 {'IBD': 0.23500000000000001, 'RA': 0.09},
 {'IBD': 0.275, 'RA': 0.09},
 {'IBD': 0.26500000000000007, 'RA': 0.12000000000000002},
 {'IBD': 0.275, 'RA': 0.1},
 {'IBD': 0.265, 'RA': 0.11000000000000001},
 {'IBD': 0.28500000000000003, 'RA': 0.1},
 {'IBD': 0.2750000000000001, 'RA': 0.09}]

In [ ]:
!pip install node2vec networkx

In [ ]:
# get full sc_ppi graph
import pandas as pd
import networkx as nx
from collections import defaultdict

ppi = pinnacle.get_ppi()
scproteins = pinnacle.get_keys()
# scproteins.head()
protein_to_cells = defaultdict(set)

for _, row in scproteins.iterrows():
    protein_to_cells[row['target']].add(row['cell type'])

# make graph
G = nx.Graph()
for _, row in ppi.iterrows():
    protein1 = row['Protein A']
    protein2 = row['Protein B']
    cell_types1 = protein_to_cells[protein1]
    cell_types2 = protein_to_cells[protein2]

    if protein1 not in G:
        G.add_node(protein1, cell_types=list(cell_types1))
    if protein2 not in G:
        G.add_node(protein2, cell_types=list(cell_types2))
    G.add_edge(protein1, protein2)

In [ ]:
# 1. Preview first few nodes and their attributes
def preview_nodes(G, n=5):
    print("First", n, "nodes and their attributes:")
    for i, (node, attr) in enumerate(G.nodes(data=True)):
        if i >= n: break
        print(f"Node: {node}")
        print(f"Attributes: {attr}\n")

# 2. Preview first few edges
def preview_edges(G, n=5):
    print("First", n, "edges:")
    for i, (node1, node2, attr) in enumerate(G.edges(data=True)):
        if i >= n: break
        print(f"Edge: {node1} -- {node2}")
        print(f"Attributes: {attr}\n")

# 3. Get basic graph statistics
def preview_graph_stats(G):
    print("Graph Statistics:")
    print(f"Number of nodes: {G.number_of_nodes()}")
    print(f"Number of edges: {G.number_of_edges()}")
    print(f"Is directed: {G.is_directed()}")
    print(f"Is weighted: any('weight' in d for u,v,d in G.edges(data=True))")

    # Sample of node attributes available
    if G.nodes():
        sample_node = list(G.nodes(data=True))[0]
        print(f"\nSample node attributes: {list(sample_node[1].keys())}")

# Combined preview
def preview_graph(G, n=5):
    print("=== Graph Preview ===\n")
    preview_graph_stats(G)
    print("\n=== Sample Nodes ===\n")
    preview_nodes(G, n)
    print("=== Sample Edges ===\n")
    preview_edges(G, n)

    # Preview cell types if they exist
    sample_cell_types = set()
    for _, attr in list(G.nodes(data=True))[:n]:
        if 'cell_types' in attr:
            sample_cell_types.update(attr['cell_types'])
    if sample_cell_types:
        print("\n=== Sample Cell Types ===")
        print(list(sample_cell_types)[:5])

preview_graph(G)

=== Graph Preview ===

Graph Statistics:
Number of nodes: 15461
Number of edges: 207640
Is directed: False
Is weighted: any('weight' in d for u,v,d in G.edges(data=True))

Sample node attributes: ['cell_types']

=== Sample Nodes ===

First 5 nodes and their attributes:
Node: FLNC
Attributes: {'cell_types': ['gut endothelial cell', 'fast muscle cell', 'fibroblast', 'cardiac endothelial cell', 'fibroblast of breast', 'smooth muscle cell', 'endothelial cell of lymphatic vessel', 'vascular associated smooth muscle cell', 'artery endothelial cell', 'hepatocyte', 'bronchial smooth muscle cell', 'myometrial cell', 'medullary thymic epithelial cell', 'endothelial cell of artery', 'skeletal muscle satellite stem cell', 'ciliary body', 'pericyte cell', 'mesothelial cell', 'tendon cell', 'cardiac muscle cell', 'lymphatic endothelial cell', 'connective tissue cell', 'cell of skeletal muscle', 'ocular surface cell', 'fibroblast of cardiac tissue']}

Node: SGCD
Attributes: {'cell_types': ['gut endot

In [ ]:
# Node2Vec benchmark class
import networkx as nx
from node2vec import Node2Vec
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, precision_recall_fscore_support, roc_auc_score
import numpy as np
import pandas as pd
from collections import defaultdict

class SingleCellNode2VecBenchmark:
    def __init__(
        self,
        dimensions=128,
        walk_length=80,
        num_walks=10,
        p=1,
        q=1,
        workers=4,
        window=10,
        cell_type=None  # Specific cell type to analyze, None for all cells
    ):
        self.dimensions = dimensions
        self.walk_length = walk_length
        self.num_walks = num_walks
        self.p = p
        self.q = q
        self.workers = workers
        self.window = window
        self.cell_type = cell_type
        self.embeddings = None
        self.classifier = LogisticRegression(max_iter=1000, class_weight='balanced')

    def fit(self, G, target_labels, train_mask=None): # input train proteins on train_mask
        """
        Fit Node2Vec embeddings and train classifier

        Args:
            G (networkx.Graph): Input PPI network with cell type information
            target_labels (dict): Dictionary mapping node IDs to target labels (0/1)
            train_mask (list): Optional list of node IDs to use for training
        """
        # Get relevant nodes for specified cell type
        # cell_nodes = self.get_cell_specific_nodes(G) # gets all cells by default

        # Generate Node2Vec embeddings on full graph
        node2vec = Node2Vec(
            G,
            dimensions=self.dimensions,
            walk_length=self.walk_length,
            num_walks=self.num_walks,
            p=self.p,
            q=self.q,
            workers=self.workers
        )

        # Train embeddings
        model = node2vec.fit(window=self.window)

        # Get embeddings for all nodes
        self.embeddings = {node: model.wv[str(node)] for node in G.nodes()}

        # Filter nodes for training based on cell type and train mask
        train_nodes = [node for node in train_mask]

        # Get training data
        X = np.array([self.embeddings[node] for node in train_nodes])
        y = np.array([target_labels[node] for node in train_nodes])

        # Train classifier
        self.classifier.fit(X, y)

    def predict(self, nodes):
        """Predict target labels for given nodes"""
        X = np.array([self.embeddings[node] for node in nodes])
        return self.classifier.predict(X)

In [ ]:
# now just loop through many seeds with same algo
out = []
scnode2vec_benchmark = SingleCellNode2VecBenchmark()
group = scdti_group.SCDTIGroup()
for i in range(1,11):
  train, dev, test = get_train_dev_test(seed=i)
  full = pd.concat([train, dev, test], axis=0, ignore_index=True)
  full_ra = full[full["disease"] == "RA"]
  full_ibd = full[full["disease"] == "IBD"]
  olabels_ra = {x["name"]:x["y"] for _, x in full_ra.iterrows()}
  olabels_ibd = {x["name"]:x["y"] for _, x in full_ibd.iterrows()}

  scnode2vec_benchmark.fit(G, olabels_ra, train_mask=train[train["disease"] == "RA"]["name"].values)
  preds = scnode2vec_benchmark.predict(test[test["disease"] == "RA"]["name"].values)
  scnode2vec_benchmark.fit(G, olabels_ibd, train_mask=train[train["disease"] == "IBD"]["name"].values)
  preds_ibd = scnode2vec_benchmark.predict(test[test["disease"] == "IBD"]["name"].values)
  test_ra = test[test["disease"] == "RA"]
  test_ibd = test[test["disease"] == "IBD"]
  test_ra["preds"] = preds
  test_ibd["preds"] = preds_ibd
  # construct preds map
  preds_map = defaultdict(int)
  for _, row in test_ra.iterrows():
    preds_map[("RA", row["cell_type_label"], row["name"])] = row["preds"]
  for _, row in test_ibd.iterrows():
    preds_map[("IBD", row["cell_type_label"], row["name"])] = row["preds"]
  test["preds"] = test.apply(lambda x: preds_map[("RA", x["cell_type_label"], x["name"])] if x["disease"] == "RA" else preds_map[("RA", x["cell_type_label"], x["name"])], axis=1)
  test.to_csv(f'/content/drive/MyDrive/pinnacle_scdti_word2vec/test_dataframe_scdti_word2vec_seed{i}B.csv', index=False)
  res = group.evaluate(test, seed=i)
  out.append(res)
out

Downloading...
100%|██████████| 2.57M/2.57M [00:00<00:00, 9.66MiB/s]
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 2.44MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:05<00:00, 36.1MiB/s]
Downloading...
100%|██████████| 20.5M/20.5M [00:00<00:00, 40.3MiB/s]
Found local copy...
Loading...
Found local copy...
Loading...
Found local copy...
Found local copy...
Downloading...


downloading pinancle zip data...


100%|██████████| 5.20M/5.20M [00:00<00:00, 21.0MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_test_preds_myeloid dendritic cell.csv
got file TS_EFO_0003767_torch_mlp_val_preds_eye photoreceptor cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_lacrimal gland functional unit cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_intestinal crypt stem cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_intermediate monocyte.csv
got file TS_EFO_0000685_torch_mlp_all_preds_cardiac endothelial cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_myofibroblast cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_erythroid progenitor.csv
got file TS_EFO_0000685_torch_mlp_test_preds_cardiac muscle cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_retinal pigment epithelial cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_respiratory goblet cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_hepatocyte.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_val_preds_hillock cell of prostate epithel

Downloading...


...

got file TS_EFO_0003767_torch_mlp_train_preds_schwann cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_vein endothelial cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_classical monocyte.csv
got file TS_EFO_0000685_torch_mlp_test_preds_type i pneumocyte.csv
got file TS_EFO_0000685_torch_mlp_train_preds_transit amplifying cell of large intestine.csv
got file TS_EFO_0000685_torch_mlp_train_preds_endothelial cell of hepatic sinusoid.csv
got file TS_EFO_0003767_torch_mlp_train_preds_pericyte cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_hepatocyte.csv
got file TS_EFO_0000685_torch_mlp_val_preds_radial glial cell.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_test_preds_regulatory t cell.csv
got file TS_EFO_0000685_torch_mlp_train_preds_naive thymus-derived cd4-positive, alpha-beta t cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_fibroblast.csv
got file TS_EFO_0000685_torch_mlp_all_preds_lymphatic endothelial cell.csv
got file TS_EFO_0000685_torch_mlp_va

100%|██████████| 6.45M/6.45M [00:00<00:00, 23.4MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_test_preds_myeloid dendritic cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_val_preds_eye photoreceptor cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_lacrimal gland functional unit cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_intestinal crypt stem cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_intermediate monocyte.csv
got file TS_EFO_0000685_torch_mlp_all_preds_cardiac endothelial cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_myofibroblast cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_erythroid progenitor.csv
got file TS_EFO_0000685_torch_mlp_test_preds_cardiac muscle cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_all_preds_retinal pigment epithelial cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_respiratory goblet cell.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_train_preds_hepatocyte.csv
got file TS_EFO_0003767_torch_

Computing transition probabilities:   0%|          | 0/15461 [00:00<?, ?it/s]

Computing transition probabilities:   0%|          | 0/15461 [00:00<?, ?it/s]